In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import matplotlib.pyplot as plt
import torchaudio
import torch
import numpy as np
import pandas as pd
import os
import pickle
import re
import torchaudio.transforms as T
import math
import librosa
import librosa.display
import matplotlib.patches as patches
from glob import glob
import util
from util import audio_file
from util import *
from Losses import FocalLoss,WeightedFocalLoss
from StackedLSTM2 import StackedLSTM
from AttentionLSTM import Attention_LSTM
from Toy_Model import ToyModel
import time
torch.manual_seed(1)

n_samples = 40
train_split = 4*n_samples//5
test_samples = n_samples - train_split
input_list, labels_list = load_data()
test_input_list = input_list[30*train_split:]
test_labels_list = labels_list[30*train_split:]
input_list = input_list[:train_split*30]
labels_list = labels_list[:train_split*30]
input_list.shape
print("done")

0
(180600,)
1
(180600,)
2
(180600,)
3
(180600,)
4
(180600,)
5
(180600,)
6
(180600,)
7
(180600,)
8
(180600,)
9
(180600,)
10
(180600,)
11
(180600,)
12
(180600,)
13
(180600,)
14
(180600,)
15
(180600,)
16
(180600,)
17
(180600,)
18
(180600,)
19
(180600,)
20
(180600,)
21
(180600,)
22
(180600,)
23
(180600,)
24
(180600,)
25
(180600,)
26
(180600,)
27
(180600,)
28
(180600,)
29
(180600,)
30
(180600,)
31
(180600,)
32
(180600,)
33
(180600,)
34
(180600,)
35
(180600,)
36
(180600,)
37
(180600,)
38
(180600,)
39
(180600,)
40
(180600,)
41
(180600,)
42
(180600,)
43
(180600,)
44
(180600,)
45
(180600,)
46
(180600,)
47
(180600,)
48
(180600,)
49
(180600,)
50
(180600,)
51
(180600,)
52
(180600,)
53
(180600,)
54
(180600,)
55
(180600,)
56
(180600,)
57
(180600,)
58
(180600,)
59
(180600,)
60
(180600,)
61
(180600,)
62
(180600,)
63


In [3]:
input_list.shape
my_model = "Vanilla_LSTM"
verbose=1

if my_model == "Attention_LSTM":
    model = Attention_LSTM()
    save_filepath = '/project/graziul/ra/ajays/LSTM_model_predictions.txt'
elif my_model == "Vanilla_LSTM":
    model = ToyModel()
    save_filepath = '/project/graziul/ra/ajays/toy_model_predictions.txt'
loss_fn = FocalLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-2)
fer_list = []
train_loss_list = []
test_loss_list = []
sample_size = 30
batch_size = model.batch_size
num_samples = input_list.size()[0]//batch_size
training_steps = 2
idx = 0
flag = 0
num_segments = 30
val_size = 30

In [4]:
#preds_file = open(save_filepath,'w')
#preds_file.truncate(0)

for val_index in range(num_samples):
    #model = StackedLSTM()
    #model = Attention_LSTM()
    if my_model == "Attention_LSTM":
        model = Attention_LSTM()
    elif my_model == "Vanilla_LSTM":
        model = ToyModel()
    #model = nn.DataParallel(model)
    loss_fn = FocalLoss()
    optimizer = torch.optim.Adam(model.parameters(), lr=1e-2)
    test_data = input_list[val_index*val_size:(val_index+1)*val_size] 
    test_labels = labels_list[val_index*val_size:(val_index+1)*val_size]
    train_data = torch.cat([input_list[:val_index*val_size], input_list[(val_index+1)*val_size:]], dim = 0)
    train_labels = torch.cat([labels_list[:val_index*val_size], labels_list[(val_index+1)*val_size:]], dim = 0)
    print(val_index)
    idx = 0
    for step in range(training_steps):
        if(idx != val_index):
            input_batch = train_data[idx*batch_size:(idx+1)*batch_size]
            labels_batch = train_labels[idx*batch_size:(idx+1)*batch_size]
            if(input_batch.size()[0] != 0):
                print(step)
                optimizer.zero_grad()
                output_hat = model(input_batch)
                print(labels_batch)
                print(output_hat)
                loss = loss_fn(output_hat, labels_batch)
                loss.backward()
                #for param in model.parameters():
                #    print(param.grad)
                print(loss)
                optimizer.step()
        idx = (idx+1)%num_samples
    with torch.no_grad():
        if (test_data.size()[0] != 0):
            preds = get_predictions(model,test_data, test_labels, batch_size)  
            fer_value = get_frame_error_rate(torch.round(preds),test_labels, verbose)
            if verbose == 0:
                fer = str(fer_value) + "\n"
            else:
                fer = "FER = " + str(fer_value[0]) + ", False_Positives = " + str(fer_value[1]) + ", False Negatives = " + str(fer_value[2]) + "\n"
            print(fer)
            #preds_file.write(fer)
#preds_file.close()



0
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5030, 0.5071, 0.5076,  ..., 0.5083, 0.5083, 0.5083],
        [0.5019, 0.5083, 0.5097,  ..., 0.5083, 0.5083, 0.5083]],
       grad_fn=<SqueezeBackward0>)
tensor(0.7099, grad_fn=<MeanBackward0>)
15
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
FER = [tensor(6.5337), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.), tensor(0.)], False_Positives = [[0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0]], False Negatives = [[0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0

2
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5400, 0.5359, 0.5299,  ..., 0.5184, 0.5184, 0.5184],
        [0.5206, 0.5218, 0.5203,  ..., 0.5183, 0.5183, 0.5183]],
       grad_fn=<SqueezeBackward0>)
tensor(-0.5846, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5539, 0.5838, 0.5975,  ..., 0.6160, 0.6160, 0.6160],
        [0.5815, 0.5923, 0.6010,  ..., 0.6163, 0.6163, 0.6163]],
       grad_fn=<SqueezeBackward0>)
tensor(0.9574, grad_fn=<MeanBackward0>)
15
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
FER = [tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tens

3
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5203, 0.5159, 0.5158,  ..., 0.5167, 0.5167, 0.5167],
        [0.5101, 0.5203, 0.5213,  ..., 0.5167, 0.5167, 0.5167]],
       grad_fn=<SqueezeBackward0>)
tensor(-0.4627, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5765, 0.5835, 0.5947,  ..., 0.6174, 0.6174, 0.6174],
        [0.5603, 0.5892, 0.5986,  ..., 0.6175, 0.6175, 0.6175]],
       grad_fn=<SqueezeBackward0>)
tensor(0.9610, grad_fn=<MeanBackward0>)
15
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
FER = [tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(92.6434), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), t

4
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5032, 0.4952, 0.4929,  ..., 0.4915, 0.4915, 0.4915],
        [0.4407, 0.4630, 0.4759,  ..., 0.4915, 0.4915, 0.4915]],
       grad_fn=<SqueezeBackward0>)
tensor(1.2833, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5755, 0.5940, 0.6021,  ..., 0.6353, 0.6353, 0.6353],
        [0.4735, 0.5278, 0.5611,  ..., 0.6351, 0.6351, 0.6351]],
       grad_fn=<SqueezeBackward0>)
tensor(1.0082, grad_fn=<MeanBackward0>)
15
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
FER = [tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tenso

5
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.4708, 0.4680, 0.4666,  ..., 0.4665, 0.4665, 0.4665],
        [0.4705, 0.4560, 0.4563,  ..., 0.4666, 0.4666, 0.4666]],
       grad_fn=<SqueezeBackward0>)
tensor(3.0172, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5153, 0.5358, 0.5565,  ..., 0.5964, 0.5964, 0.5964],
        [0.4983, 0.5036, 0.5282,  ..., 0.5968, 0.5968, 0.5968]],
       grad_fn=<SqueezeBackward0>)
tensor(0.9074, grad_fn=<MeanBackward0>)
15
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
FER = [tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tenso

...

23
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5126, 0.5180, 0.5166,  ..., 0.5098, 0.5098, 0.5098],
        [0.5062, 0.5116, 0.5144,  ..., 0.5099, 0.5099, 0.5099]],
       grad_fn=<SqueezeBackward0>)
tensor(0.0035, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5607, 0.5867, 0.6002,  ..., 0.6397, 0.6397, 0.6397],
        [0.5962, 0.6098, 0.6174,  ..., 0.6395, 0.6395, 0.6395]],
       grad_fn=<SqueezeBackward0>)
tensor(1.0202, grad_fn=<MeanBackward0>)
5
0
1
2
3
4
FER = [tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(100.), tensor(99.9751)], False_Positives = [[0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 

24
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.4872, 0.4832, 0.4849,  ..., 0.4931, 0.4931, 0.4931],
        [0.4804, 0.4876, 0.4885,  ..., 0.4931, 0.4931, 0.4931]],
       grad_fn=<SqueezeBackward0>)
tensor(1.1757, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5620, 0.5742, 0.5890,  ..., 0.6198, 0.6198, 0.6198],
        [0.5646, 0.5783, 0.5908,  ..., 0.6198, 0.6198, 0.6198]],
       grad_fn=<SqueezeBackward0>)
tensor(0.9667, grad_fn=<MeanBackward0>)
25
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5217, 0.5111, 0.5079,  ..., 0.5067, 0.5067, 0.5067],
        [0.4989, 0.5033, 0.5043,  ..., 0.5067, 0.5067, 0.5067]],
       grad_fn=<SqueezeBackward0>)
tensor(0.2313, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
te

tensor(0.8320, grad_fn=<MeanBackward0>)
38
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5265, 0.5140, 0.5091,  ..., 0.5047, 0.5047, 0.5047],
        [0.4993, 0.5039, 0.5068,  ..., 0.5047, 0.5047, 0.5047]],
       grad_fn=<SqueezeBackward0>)
tensor(0.3609, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5378, 0.5641, 0.5798,  ..., 0.6064, 0.6064, 0.6064],
        [0.5542, 0.5707, 0.5814,  ..., 0.6064, 0.6064, 0.6064]],
       grad_fn=<SqueezeBackward0>)
tensor(0.9325, grad_fn=<MeanBackward0>)
39
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5001, 0.4951, 0.4921,  ..., 0.4829, 0.4829, 0.4830],
        [0.4937, 0.4899, 0.4877,  ..., 0.4830, 0.4830, 0.4830]],
       grad_fn=<SqueezeBackward0>)
tensor(1.8776, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
   

tensor(1.2380, grad_fn=<MeanBackward0>)
52
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5250, 0.5083, 0.4974,  ..., 0.4872, 0.4872, 0.4873],
        [0.4918, 0.4929, 0.4910,  ..., 0.4873, 0.4873, 0.4873]],
       grad_fn=<SqueezeBackward0>)
tensor(1.5768, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
tensor([[0.5625, 0.5702, 0.5759,  ..., 0.6106, 0.6106, 0.6106],
        [0.4714, 0.5271, 0.5564,  ..., 0.6105, 0.6105, 0.6105]],
       grad_fn=<SqueezeBackward0>)
tensor(0.9425, grad_fn=<MeanBackward0>)
53
0
tensor([[  0.,  82., 215.,  ...,   0.,   0.,   0.],
        [  0.,   0.,   0.,  ...,   0.,   0.,   0.]])
tensor([[0.5499, 0.5479, 0.5417,  ..., 0.5367, 0.5367, 0.5367],
        [0.5629, 0.5488, 0.5448,  ..., 0.5367, 0.5367, 0.5367]],
       grad_fn=<SqueezeBackward0>)
tensor(-1.8572, grad_fn=<MeanBackward0>)
1
tensor([[0., 0., 0.,  ..., 0., 0., 0.],
  

KeyboardInterrupt: 